<a href="https://colab.research.google.com/github/raphkwok/Intraoperative-Measurement-Tool/blob/main/Polyphonic_Demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Libraries and Installs

In [ ]:
# General Import
from google.colab import userdata
import cv2, os
import numpy as np
from PIL import Image
import torch
import torchvision.ops as ops
from tqdm import tqdm
import json
from moviepy.editor import VideoFileClip
from collections import defaultdict
import plotly.graph_objects as go
import matplotlib.pyplot as plt



# File Upload
from google.colab import files

  if event.key is 'enter':



# Calibration

In [ ]:
# Upload images
uploaded = files.upload()

# Check file type annd convert if needed
for image_file in uploaded.keys():
    image_path = "/content/" + image_file
    try:
        with Image.open(image_path) as img:
            img = img.convert('RGB')
            img.save(image_path + ".png", "PNG")
    except Exception as e:
        print(f"Failed to process {image_file}: {e}")


# Chessboard dimensions
chessboard_size = (10, 7)
square_size = 23

# Prepare object points
objp = np.zeros((chessboard_size[0] * chessboard_size[1], 3), np.float32)
objp[:, :2] = np.mgrid[0:chessboard_size[0], 0:chessboard_size[1]].T.reshape(-1, 2)
objp *= square_size

# Arrays to store object points and image points
objpoints = []
imgpoints = []

# Display images - to check corners
def display_frame(frame, title="Image"):
    plt.figure(figsize=(10, 8))
    plt.imshow(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))
    plt.title(title)
    plt.axis('off')
    plt.show()

# Process images
for image_file in uploaded.keys():
    image_path = "/content/" + image_file + ".png"
    # Read the image
    img = cv2.imread(image_file)
    if img is None:
        print(f"Failed to load {image_file}")
        continue

    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)
    gray = cv2.equalizeHist(gray)

    # Find the chessboard corners
    ret, corners = cv2.findChessboardCorners(gray, chessboard_size,
                                         cv2.CALIB_CB_ADAPTIVE_THRESH +
                                         cv2.CALIB_CB_NORMALIZE_IMAGE +
                                         cv2.CALIB_CB_FAST_CHECK)

    if ret:
        # Refine corner positions
        corners2 = cv2.cornerSubPix(gray, corners, (11, 11), (-1, -1),
                                    criteria=(cv2.TERM_CRITERIA_EPS + cv2.TERM_CRITERIA_MAX_ITER, 30, 0.001))
        objpoints.append(objp)
        imgpoints.append(corners2)
    else:
        print(f"No corners detected in {image_file}")

if len(objpoints) > 0 and len(imgpoints) > 0:
    ret, camera_matrix, dist_coeffs, rvecs, tvecs = cv2.calibrateCamera(
        objpoints, imgpoints, gray.shape[::-1], None, None
    )
    print("Camera matrix:")
    print(camera_matrix)
    print("Distortion coefficients:")
    print(dist_coeffs)
else:
    print("No valid images found. Calibration not performed.")


# Mean Reprojection Error
total_error = 0
for i in range(len(objpoints)):
    imgpoints2, _ = cv2.projectPoints(objpoints[i], rvecs[i], tvecs[i], camera_matrix, dist_coeffs)
    error = cv2.norm(imgpoints[i], imgpoints2, cv2.NORM_L2) / len(imgpoints2)
    total_error += error

mean_error = total_error / len(objpoints)
print(f"Mean Reprojection Error: {mean_error}")

Saving Untitled.png to Untitled.png
Saving Untitled 2.png to Untitled 2.png
Saving Untitled 3.png to Untitled 3.png
Saving Untitled 4.png to Untitled 4.png
Saving Untitled 5.png to Untitled 5.png
Saving Untitled 6.png to Untitled 6.png
Saving Untitled 7.png to Untitled 7.png
Saving Untitled 8.png to Untitled 8.png
Saving Untitled 9.png to Untitled 9.png
Saving Untitled 10.png to Untitled 10.png
Saving Untitled 11.png to Untitled 11.png
Saving Untitled 12.png to Untitled 12.png
Saving Untitled 13.png to Untitled 13.png
Saving Untitled 14.png to Untitled 14.png
Saving Untitled 15.png to Untitled 15.png
Saving Untitled 16.png to Untitled 16.png
Saving Untitled 17.png to Untitled 17.png
Saving Untitled 18.png to Untitled 18.png
Saving Untitled 19.png to Untitled 19.png
Saving Untitled 20.png to Untitled 20.png
No corners detected in Untitled 6.png
Camera matrix:
[[1.25924841e+03 0.00000000e+00 8.84447816e+02]
 [0.00000000e+00 1.32854769e+03 5.43795452e+02]
 [0.00000000e+00 0.00000000e+00 1

In [ ]:
K = camera_matrix

fx = K[0, 0]
uploaded = files.upload()
filename = next(iter(uploaded))

# Read sample image
img = cv2.imread(filename)
h, w = img.shape[:2]
os.remove(filename)

print(h, w)

Saving Untitled 8.png to Untitled 8 (1).png
1080 1920


# File Upload

In [ ]:
print("JSON Annotations:")
uploaded = files.upload()
json_path = next(iter(uploaded))


print("Video File:")
uploaded = files.upload()
video_path = next(iter(uploaded))



JSON Annotations:


Saving 4a8ba88e-111b-4c46-acad-daa985989be8.json to 4a8ba88e-111b-4c46-acad-daa985989be8 (1).json
Video File:


Saving B162video2_trim-silent.mp4 to B162video2_trim-silent (1).mp4


# JSON Import

In [ ]:
# Load and parse the JSON content
with open(json_path, "r") as f:
    data = json.load(f)

# Prepare lists to store annotations
left_grasper_polygons = []
right_grasper_polygons = []

# Navigate the nested structure and extract polygons
data_units = data[0]['data_units']
video_data = next(iter(data_units.values()))
labels = video_data['labels']

# Loop through each frame's annotations
for frame_id, frame_data in labels.items():
    frame_number = int(frame_id)
    for obj in frame_data['objects']:
        name = obj.get('name', '').lower()
        polygons = obj.get('polygon')
        if not polygons:
            continue

        points = [(v['x'], v['y']) for k, v in polygons.items()]
        if 'left' in name:
            left_grasper_polygons.append((frame_number, points))
        elif 'right' in name:
            right_grasper_polygons.append((frame_number, points))

frame_polygons = defaultdict(lambda: {'left': [], 'right': []})
for frame_num, pts in left_grasper_polygons:
    frame_polygons[frame_num]['left'].append(pts)
for frame_num, pts in right_grasper_polygons:
    frame_polygons[frame_num]['right'].append(pts)

In [ ]:
# VISUALIZE ANNOTATIONS

left_grasper = []
right_grasper = []

cap = cv2.VideoCapture(video_path)
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out_path = "annotated_video.mp4"
fps = cap.get(cv2.CAP_PROP_FPS)
width  = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
out = cv2.VideoWriter(out_path, fourcc, fps, (width, height))

frame_idx = 0
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    polygons = frame_polygons.get(frame_idx, {})
    for pts in polygons.get('left', []):
        pts_px = np.array(
            [[int(x * width), int(y * height)] for (x, y) in pts],
            dtype=np.int32
        )
        cv2.polylines(frame, [pts_px], isClosed=True, color=(0,255,0), thickness=2)

    for pts in polygons.get('right', []):
        pts_px = np.array(
            [[int(x * width), int(y * height)] for (x, y) in pts],
            dtype=np.int32
        )
        cv2.polylines(frame, [pts_px], isClosed=True, color=(0,0,255), thickness=2)


    out.write(frame)
    frame_idx += 1

cap.release()
out.release()

files.download(out_path)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# P4P Functions

In [ ]:
# Taking 2D points and getting 3D coords
def estimate_distance(lpoints, rpoints):

  # lpoints = np.array(lpoints, dtype=np.float32)
  # rpoints = np.array(rpoints, dtype=np.float32)

  lbox = get_rectangle(lpoints)
  rbox = get_rectangle(rpoints)

  # Get the 3D coordinates of image points
  left_coords = compute_3d_coordinates(K, lbox, [l_width, l_length])
  right_coords = compute_3d_coordinates(K, rbox, [r_width, r_length])


  lowest_distance = np.inf
  lowest_pair = None

  for i in range(len(left_coords)):
    lp = left_coords[i]
    for j in range(len(right_coords)):
      rp = right_coords[j]
      # print(f"Distance between {lbox[i]} and {rbox[j]}: {np.linalg.norm(lp - rp)}")
      if np.linalg.norm(lp - rp) < lowest_distance:
        lowest_distance = np.linalg.norm(lp - rp)
        lowest_pair = (lbox[i], rbox[j])

  return(lowest_distance, lowest_pair, lbox, rbox)



In [ ]:
# To reorder the bounding box points for the P4P solver
def reorder_rectangle(points):
  # Ensure input points are a NumPy array
  points = np.array(points, dtype=np.float32)

  shortest_distance = np.inf
  shortest_index = None
  for i in range(4):
    p1 = points[i]
    p2 = points[(i + 1) % 4]
    distance = np.linalg.norm(p1 - p2)
    if distance <= shortest_distance:
      shortest_distance = distance
      shortest_index = i

  points = np.roll(points, -shortest_index, axis=0)


  return points


In [ ]:
def get_rectangle(points):
  rect = cv2.minAreaRect(points)

  # Get the 4 corner points of the bounding box
  box = cv2.boxPoints(rect)

  # Convert the points to integers
  box = box.astype(np.intp)

  reordered_points = reorder_rectangle(box)

  return reorder_rectangle(box)
  return reordered_points


In [ ]:
def compute_3d_coordinates(K, points, dimensions):
  width, height = dimensions
  object_points = np.array([
      [-width/2, -height/2, 0],
      [width/2, -height/2, 0],
      [width/2, height/2, 0],
      [-width/2, height/2, 0]
  ], dtype=np.float32)

  # Convert 2D screen points to numpy array
  image_points = np.array(points, dtype=np.float32)

  # Use solvePnP to find rotation and translation vectors
  success, rvec, tvec = cv2.solvePnP(object_points, image_points, K, dist_coeffs, None, None, False, cv2.SOLVEPNP_ITERATIVE)
  if not success:
      raise ValueError("Could not solve PnP problem")

  # Convert rotation vector to rotation matrix
  R, _ = cv2.Rodrigues(rvec)

  # Transform 3D object points to the camera coordinate system
  camera_coordinates = (R @ object_points.T + tvec).T

  return camera_coordinates

# Input Interaction

In [ ]:
# INPUT VALUES

# L Dimensions
l_length = 3.2
l_width = 0.5

# R Dimensions
r_length = 3.2
r_width = 0.5

In [ ]:
cap = cv2.VideoCapture(video_path)
width  = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps    = cap.get(cv2.CAP_PROP_FPS)
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out    = cv2.VideoWriter('annotated_output.mp4', fourcc, fps, (width, height))

# 2) Loop through frames
frame_idx = 0
while True:
  ret, frame = cap.read()
  if not ret:
      break


  # Get Values
  polys      = frame_polygons.get(frame_idx, {'left': [], 'right': []})
  left_norm  = polys.get('left', [])
  right_norm = polys.get('right', [])


  # Filter out empty frames
  if left_norm and right_norm:

    # Draw CV Predictions
    lpoints = np.array(
        [[int(x * width), int(y * height)] for (x, y) in left_norm[0]],
        dtype=np.int32
    )
    cv2.polylines(frame, [lpoints], isClosed=True, color=(0,255,0), thickness=2)

    rpoints = np.array(
        [[int(x * width), int(y * height)] for (x, y) in right_norm[0]],
        dtype=np.int32
    )
    cv2.polylines(frame, [rpoints], isClosed=True, color=(0,255,0), thickness=2)


    # Estimate Distance
    dist, (ptL, ptR), lbox, rbox = estimate_distance(lpoints, rpoints)

    # Draw Box
    cv2.polylines(frame, [lbox.astype(int)], isClosed=True, color=(0,0,255), thickness=2)
    cv2.polylines(frame, [rbox.astype(int)], isClosed=True, color=(0,0,255), thickness=2)

    # Draw line and text
    ptL = tuple(ptL.astype(int))
    ptR = tuple(ptR.astype(int))

    cv2.line(frame, ptL, ptR, (255,0,0), 2)

    # Text label above midpoint
    mx, my = ( (ptL[0]+ptR[0])//2, (ptL[1]+ptR[1])//2 - 10 )
    cv2.putText(frame,
                f"{dist:.2f} cm",
                (mx, my),
                cv2.FONT_HERSHEY_SIMPLEX,
                0.6,
                (255,0,0),
                2,
                cv2.LINE_AA)

    # ----- SAMPLE UI MOCKUP -----

    # UI Parameters
    gauge_max   = 80.0               # the full‐scale value (80 cm)
    gauge_start = 30.0               # the white “baseline” (30 cm)
    gauge_radius    = 80             # radius in pixels
    gauge_thickness = 12              # ring thickness in pixels
    margin          = 100             # distance from frame edges

    # center in top-right
    cx = width  - margin - gauge_radius
    cy = margin + gauge_radius

    # get angles
    start_angle = -90  # 12 o’clock
    white_span  = (gauge_start / gauge_max) * 360
    red_span    = (dist        / gauge_max) * 360

    white_end = int(start_angle + white_span)
    red_end   = int(white_end     + red_span)

    # background ring (grey)
    cv2.ellipse(frame,
                (cx, cy),
                (gauge_radius, gauge_radius),
                0, 0, 360,
                (200,200,200),
                gauge_thickness)

    # white baseline arc
    cv2.ellipse(frame,
                (cx, cy),
                (gauge_radius, gauge_radius),
                0,
                start_angle,
                white_end,
                (255,255,255),
                gauge_thickness)

    # red dist arc
    cv2.ellipse(frame,
                (cx, cy),
                (gauge_radius, gauge_radius),
                0,
                white_end,
                red_end,
                (0,0,255),
                gauge_thickness)

    # divider line
    line_len = gauge_radius // 2
    cv2.line(frame,
            (cx - line_len//2, cy),
            (cx + line_len//2, cy),
            (255,255,255), 2)

    # two-line text: “30+dist” above, “80” below
    num = gauge_start + dist
    txt1 = f"{num:.1f}"
    txt2 = f"{int(gauge_max)}"
    # measure sizes
    (w1,h1),_ = cv2.getTextSize(txt1, cv2.FONT_HERSHEY_SIMPLEX, 0.8, 2)
    (w2,h2),_ = cv2.getTextSize(txt2, cv2.FONT_HERSHEY_SIMPLEX, 0.8, 2)
    # positions
    y1 = cy - 10                     # a bit above center
    y2 = cy + h2 + 10                # a bit below center
    x1 = cx - w1//2
    x2 = cx - w2//2
    # draw
    cv2.putText(frame, txt1, (x1, y1),
                cv2.FONT_HERSHEY_SIMPLEX, 0.8, (255,255,255), 2, cv2.LINE_AA)
    cv2.putText(frame, txt2, (x2, y2),
                cv2.FONT_HERSHEY_SIMPLEX, 0.8, (255,255,255), 2, cv2.LINE_AA)

  out.write(frame)
  frame_idx += 1

cap.release()
out.release()

# 3) Download the result
files.download('annotated_output.mp4')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Manual Input

In [ ]:
# Upload and read an image
uploaded = files.upload()
filename = next(iter(uploaded))

max_size = 1000
image = Image.open(filename)
aspect_ratio = image.width / image.height

if image.width > max_size or image.height > max_size:
    if image.width > image.height:
        new_width = max_size
        new_height = int(max_size / aspect_ratio)
    else:
        new_height = max_size
        new_width = int(max_size * aspect_ratio)
    image = image.resize((new_width, new_height))

image_array = np.array(image)

# Lists for points
left_points = []
right_points = []

fig = go.Figure()
fig.add_trace(go.Image(z=image_array))

fig.add_trace(go.Scatter(x=[], y=[], mode="markers", marker=dict(color="red", size=5), name="Left Points"))
fig.add_trace(go.Scatter(x=[], y=[], mode="markers", marker=dict(color="blue", size=5), name="Right Points"))

fig.update_layout(
    clickmode='event+select',  # Enable click events
    margin=dict(l=0, r=0, t=0, b=0),  # Remove margins
    height=image_array.shape[0],
    width=image_array.shape[1]
)

# Show the figure
fig.show()



# Define a JavaScript handler for click events
from IPython.display import display, Javascript

def log_js():
    return Javascript(f"""
        var mousePos = {{x: null, y: null}};
        var leftPoints = [];
        var rightPoints = [];
        var myPlot = document.querySelector('.plotly-graph-div');

        // Track mouse position
        myPlot.on('plotly_hover', function(data) {{
            mousePos.x = data.points[0].x;
            mousePos.y = data.points[0].y;
        }});

        // Log points on keypress
        document.addEventListener('keydown', function(event) {{
            if (!mousePos.x || !mousePos.y) return;  // Ensure we have a valid mouse position

            if (event.key === 'l') {{
                // Log left point
                leftPoints.push([mousePos.x, mousePos.y]);
                var xs = leftPoints.map(pt => pt[0]);
                var ys = leftPoints.map(pt => pt[1]);
                Plotly.restyle(myPlot, {{x: [xs], y: [ys]}}, [1]);  // Update left points trace
                google.colab.kernel.invokeFunction('notebook.add_left_click', [mousePos.x, mousePos.y], {{}});
            }} else if (event.key === 'r') {{
                // Log right point
                rightPoints.push([mousePos.x, mousePos.y]);
                var xs = rightPoints.map(pt => pt[0]);
                var ys = rightPoints.map(pt => pt[1]);
                Plotly.restyle(myPlot, {{x: [xs], y: [ys]}}, [2]);  // Update right points trace
                google.colab.kernel.invokeFunction('notebook.add_right_click', [mousePos.x, mousePos.y], {{}});
            }} else if (event.key === ' ') {{
                // Trigger Python function based on left and right points
                google.colab.kernel.invokeFunction('notebook.process_points', [leftPoints, rightPoints], {{}});
            }}
        }});
    """)

def add_left_click(x, y):
    left_points.append((x, y))  # Append to left points list
    print(f"Left Click Logged: ({x}, {y})")

def add_right_click(x, y):
    right_points.append((x, y))  # Append to right points list
    print(f"Right Click Logged: ({x}, {y})")


def test(left_points, right_points):
  print(left_points)
  print(right_points)
  # return([left_points, right_points])

def process_points(left_points, right_points):
    print("Estimating Distance")
    lpoints = np.array(left_points, dtype=np.float32)
    rpoints = np.array(right_points, dtype=np.float32)
    print(lpoints.shape)
    print(rpoints)

    dist, (lboxpoint, rboxpoint) = estimate_distance(lpoints, rpoints)
    print(left_points)
    print(right_points)
    print(f"Distance: {dist}")

from google.colab import output
output.register_callback('notebook.add_left_click', add_left_click)
output.register_callback('notebook.add_right_click', add_right_click)
output.register_callback('notebook.process_points', process_points)


# Add JavaScript for logging clicks
display(log_js())


Saving Untitled 7.png to Untitled 7 (1).png


<IPython.core.display.Javascript object>

Left Click Logged: (180, 263)
Left Click Logged: (411, 148)
Left Click Logged: (296, 410)
Right Click Logged: (613, 317)
Right Click Logged: (699, 306)
Right Click Logged: (737, 398)
Estimating Distance
(3, 2)
[[613. 317.]
 [699. 306.]
 [737. 398.]]
[[180, 263], [411, 148], [296, 410]]
[[613, 317], [699, 306], [737, 398]]
Distance: 5.041909102637931
